In [1]:
pip install pyperclip

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 23.0.1 -> 23.1.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [2]:
pip install beautifulsoup4

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 23.0.1 -> 23.1.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [3]:
pip install selenium

Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 23.0.1 -> 23.1.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [ ]:
import datetime
import time
import pyperclip
import pandas as pd
from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.action_chains import ActionChains
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
import random
import re
from bs4 import BeautifulSoup

# 크롬 웹 드라이버의 경로를 설정
driver_path = 'C:/Users/dlxod/chromedriver.exe'  # 크롬 드라이버 경로 입력
options = webdriver.ChromeOptions()
options.add_argument("--headless")  # 브라우저 숨기기
driver = webdriver.Chrome(driver_path, options=options)

# 네이버 로그인 페이지 접속
driver.get("https://nid.naver.com/nidlogin.login")

# 로그인 정보
login = {
    "id": "dlxodus890",  # 네이버 아이디
    "pw": ""  # 네이버 비밀번호
}

# 로그인 정보 입력 함수
def clipboard_input(user_xpath, user_input):
    temp_user_input = pyperclip.paste()

    pyperclip.copy(user_input)
    driver.find_element(By.XPATH, user_xpath).click()
    ActionChains(driver).key_down(Keys.CONTROL).send_keys('v').key_up(Keys.CONTROL).perform()

    pyperclip.copy(temp_user_input)
    time.sleep(1)

# id, pw 입력 후 클릭
clipboard_input('//*[@id="id"]', login.get("id"))
clipboard_input('//*[@id="pw"]', login.get("pw"))
driver.find_element(By.XPATH, '//*[@id="log.login"]').click()

time.sleep(10)

# 여기서부터 네이버 카페 크롤링 코드

# 결과 저장 경로
save_path = "C:/Users/dlxod/수만휘_크롤링"

address_list = []
page = 197

# 카페 정보 
cafe = {
    'name': "수능날만점시험지를휘날리자",                                # 카페 이름
    'page_link':"https://cafe.naver.com/suhui",                        # 주소
    'board_link':f"https://cafe.naver.com/ArticleList.nhn?search.clubid=10197921&search.menuid=3847&search.boardtype=L&search.totalCount=151&search.cafeId=10197921&search.page={page}",             # 게시판 주소
    'keywords':"수시 결과 기록+수기"                                    # 키워드 설정
}

# 카페 주소 입력
driver.get(cafe['board_link'])

# 키워드 수집 정보
num_per_page = 15  # 페이지당 게시글 갯수 (default: 15개)

l = True
while l:
    time.sleep(random.randint(0, 5))

    driver.switch_to.frame("cafe_main")  # iframe의 name 속성을 사용하여 전환
    # 현재 페이지의 html 불러오기
    r = driver.page_source
    page_html = BeautifulSoup(r, "html.parser")

    # iframe 내부에서 article-board m-tcol-c를 찾기 위해 수정
    content = page_html.find_all("div", class_="article-board m-tcol-c")[1].find('table').find('tbody')
    body = content.find_all("tr")

    # 게시글 정보 저장하기
    for x in body:
        temp_dict = {}
        if x.find("div", class_="board-number") is not None:
            temp_dict['no'] = x.find("div", class_="inner_number").text.strip()
            temp_dict['title'] = x.find("div", class_="board-list").find("div", class_="inner_list").find('a', class_='article').text.strip().replace('  ', '').replace('\n', '')
            temp_dict['link'] = x.find("div", class_="board-list").find("div", class_="inner_list").find('a', class_='article').get('href')
            temp_dict['name'] = x.find("td", class_="td_name").find('a', class_='m-tcol-c').text.strip()
            temp_dict['date'] = x.find("td", class_="td_date").text.strip()
            temp_dict['view'] = x.find("td", class_="td_view").text.strip()
         
            # ※ 게시글 들어가서 내용 크롤링하는 부분
            driver.switch_to.default_content()  # iframe을 빠져나와 기본 컨텐츠로 전환
            #driver.get(temp_dict['link'])
            driver.get('https://cafe.naver.com' + temp_dict['link'])
            time.sleep(random.randint(0, 15))
            driver.switch_to.frame("cafe_main")  # iframe 내부로 다시 진입
            post_content = driver.page_source
            post_html = BeautifulSoup(post_content, "html.parser")

            element = post_html.find("div", class_="se-component se-text se-l-default")
            if element is not None:
                paragraphs = element.find_all("p", class_=re.compile(r"se-text-paragraph(se-text-paragraph-align-)?"))
                content = [p.text.strip() for p in paragraphs]
                temp_dict['content'] = '\n'.join(content)
            else:
                temp_dict['content'] = ""
            
            address_list.append(temp_dict)
    print("(현재시각) " + str(datetime.datetime.now()) + ": " + str(page) + " page done")

    # 다음 페이지로 넘어가기
    driver.implicitly_wait(1)
    try:
        if page <= 299:  # 1페이지부터 300페이지까지 크롤링
            # 페이지 이동
            page += 1
            driver.get(f"https://cafe.naver.com/ArticleList.nhn?search.clubid=10197921&search.menuid=3847&search.boardtype=L&search.totalCount=151&search.cafeId=10197921&search.page={page}")

            # 대기 시간 추가
            time.sleep(random.randint(0, 10))
        else:
            l = False  

    except:
        print("크롤링 중 오류 발생")
        l = False

    finally:
        address_df = pd.DataFrame(address_list)
        address_df['idx_no'] = range(1, len(address_df) + 1)  # 조인할 키 값
        address_df.to_csv(save_path + ".csv", index=False, encoding='utf-8-sig')
        print("(현재시각) " + str(datetime.datetime.now()) + ": done")

if len(set(address_df['no'])) != len(address_df):
    print("게시글 번호에 중복 존재")
print("검색게시글수:", address_df.shape)
display(address_df.head())

C:\Users\dlxod\AppData\Local\Temp\ipykernel_8088\1820190417.py:19: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(driver_path, options=options)


(현재시각) 2023-06-06 03:05:32.344038: 197 page done
(현재시각) 2023-06-06 03:05:34.053220: done
(현재시각) 2023-06-06 03:07:38.375019: 198 page done
(현재시각) 2023-06-06 03:07:39.157840: done
(현재시각) 2023-06-06 03:09:42.149985: 199 page done
(현재시각) 2023-06-06 03:09:43.832614: done
(현재시각) 2023-06-06 03:11:48.148814: 200 page done
(현재시각) 2023-06-06 03:11:55.820784: done
(현재시각) 2023-06-06 03:13:51.287735: 201 page done
(현재시각) 2023-06-06 03:14:00.921564: done
(현재시각) 2023-06-06 03:15:47.871532: 202 page done
(현재시각) 2023-06-06 03:15:56.521112: done
(현재시각) 2023-06-06 03:17:45.555244: 203 page done
(현재시각) 2023-06-06 03:17:49.292236: done
(현재시각) 2023-06-06 03:20:33.234716: 204 page done
(현재시각) 2023-06-06 03:20:37.911914: done
(현재시각) 2023-06-06 03:22:13.545601: 205 page done
(현재시각) 2023-06-06 03:22:21.260778: done
(현재시각) 2023-06-06 03:24:30.436310: 206 page done
(현재시각) 2023-06-06 03:24:34.256140: done
(현재시각) 2023-06-06 03:26:15.219510: 207 page done
(현재시각) 2023-06-06 03:26:17.923375: done
(현재시각) 2023-06-06 03:

no                        title   
0  26259021              경기 하위권 일반고 수시결과  \
1  26259017           지방 일반고 3.3의 6광탈 수시   
2  26259001               중앙대 기계vs시립대 도시   
3  26259000  2.97 일반고 문과의 최종 수시결과 잘간건가요?   
4  26258980              일반고 내신 4의 수시광탈기   

                                                link         name   
0  /ArticleRead.nhn?clubid=10197921&page=197&menu...         시대건대  \
1  /ArticleRead.nhn?clubid=10197921&page=197&menu...       야생의메타몽   
2  /ArticleRead.nhn?clubid=10197921&page=197&menu...      예비야 돌아라   
3  /ArticleRead.nhn?clubid=10197921&page=197&menu...  대학입시파이팅22학번   
4  /ArticleRead.nhn?clubid=10197921&page=197&menu...        하이데거숲   

          date   view                                            content   
0  2021.12.29.  1,409  1. 입시결과 요약(합격 또는 불합격한 대학명/ 학과 / 전형)\n​\n1. 한양대...  \
1  2021.12.29.  3,921  1. 입시결과 요약(합격 또는 불합격한 대학명/ 학과 / 전형)\n​\n동국대 법학...   
2  2021.12.29.    955  중앙대 기계공학부에서 오늘 최종추합전화왔는데\n​\n중앙대 기계 vs 시립대 도시공...   
3  2021.12.29.  1,019  1. 입시결과 요약(합격 또는 불합격한 대학명/ 학과 / 전형)\n​\n1 , 건국...   
4  2021.12.29.  1,412  1. 입시결과 요약(합격 또는 불합격한 대학명/ 학과 / 전형)\n6논술\n인하대 ...   

   idx_no  
0       1  
1       2  
2       3  
3       4  
4       5

In [2]:
import pandas as pd

# CSV 파일 경로
csv_file = '수만휘_칼럼분류.csv'

# CSV 파일 읽기
df = pd.read_csv(csv_file)

# 각 열의 결측치 수 확인
missing_values = df.isna().sum()

num_rows = len(df)
print("Number of rows:", num_rows)

# 결측치 수 출력
print("결측치 출력: ", missing_values)


Number of rows: 2302
결측치 출력:  no                     0
title                  0
link                   0
name                   0
date                   0
view                   0
content                0
idx_no                 0
1. 입시결과 요약             0
2. 출신고교 종류             0
3. 내신/수능점수             0
4. 스펙                  0
5. 후배들에게 전하고 싶은 말      0
6. 수험 수기             229
dtype: int64


In [22]:
import pandas as pd

# 첫 번째 CSV 파일 불러오기
df1 = pd.read_csv('TextMining_수만휘_수시게시판_통합.csv')

# idx_no 칼럼 재조정
df1['idx_no'] = range(1, len(df1) + 1)

# 결과 확인
print(df1)

# 새로운 CSV 파일로 저장
df1.to_csv('TextMining_수만휘_수시게시판_통합.csv', index=False, encoding='utf-8-sig')


            no                 title   
0     27106679    일반고 문과 1.83의 수시 기록  \
1     27106678  어문계열 대학결정 조언 부탁드립니다🙏   
2     27106667        단대 논술 토목 빠지시는분   
3     27106563       아주대 고른기회1 화공 예비   
4     27106446         강원대 예비 빠지시는 분   
...        ...                   ...   
4510  27107215                   경상대   
4511  27107125            단국대 천안캠 예비   
4512  27106988                   부경대   
4513  27106926    5 논술 재수러의 개망한 수시결과   
4514  27106850         경희대 원공 최초합!!!   

                                                   link      name   
0     /ArticleRead.nhn?clubid=10197921&page=110&menu...    소송소송소송  \
1     /ArticleRead.nhn?clubid=10197921&page=110&menu...      aexl   
2     /ArticleRead.nhn?clubid=10197921&page=110&menu...  Sjdjdioe   
3     /ArticleRead.nhn?clubid=10197921&page=110&menu...       화공며   
4     /ArticleRead.nhn?clubid=10197921&page=110&menu...  너도나도재수없어   
...                                                 ...       ...   
4510  /ArticleRead.nhn?clubid=101979

In [19]:
## 폴더 안에 여러개의 csv파일 모아서 하나로 합치는 코드
import pandas as pd
import glob

# CSV 파일 경로
file_paths = glob.glob('C:/Users/dlxod/TextMining_수만휘_수시게시판/*.csv')

# 빈 DataFrame 생성
combined_df = pd.DataFrame()

# 파일 병합 및 idx_no 재조정
for idx, file_path in enumerate(file_paths, start=1):
    df = pd.read_csv(file_path)
    df['idx_no'] = range(idx, idx + len(df))
    combined_df = pd.concat([combined_df, df], ignore_index=True)

# 결과 저장
combined_df.to_csv('TextMining_수만휘_수시게시판_통합.csv', index=False, encoding='utf-8-sig')



In [20]:
# 1번 입시결과요약 ~대 or ~대학교 단어 나올 시 구분하는 모델
# 단점 : 대 가 들어있는 단어 앞에서 줄넘김을 해야하는데, 대->\n으로 바꿔버림

import pandas as pd
import re

# CSV 파일 불러오기
data = pd.read_csv('수만휘_칼럼분류.csv')

# "1. 입시결과 요약" 열에서 텍스트 끊어서 "new_col"에 저장
results = []
summary_column = data['1. 입시결과 요약']
for text in summary_column:
    if pd.notnull(text):  # NaN 값이 아닌 경우에만 처리
        # 정규표현식을 사용하여 '대' 또는 '대학교'가 포함된 단어를 구분자로 사용하여 텍스트를 끊어줌
        split_texts = re.split(r'대학교|대', text)
        formatted_text = '\n'.join(split_texts)
        results.append(formatted_text)

# "new_col" 열을 DataFrame에 추가
data['new_col'] = results

# 결과 출력
print(data['new_col'])

# 새로운 CSV 파일로 저장
data.to_csv('새로운_파일경로.csv', index=False, encoding='utf-8-sig')


0         한양\n 정책학과 일반 - 불합  경희\n 사회학과 교과 - 불합  시립\n 도...
1                                                        
2                                            예비 아주\n 화공  
3          고려\n 수학과 학우 학종 1차 불합 한양\n 수학과 학종 불합 경희\n 수학...
4         충북\n 도시공학과 일반 교과 최초합 전북\n 도시공학과 일반 교과 최초합 충남...
                              ...                        
2988        가천\n 식품생명공학과 사회기여자전형 - 1단계 합격 예비3번  가천\n 자...
2989      한국교원\n 일반사회교육과 학생부종합전형 예비14번9번까지 추합됨11번까지 추합...
2990       단국\n 죽전 / 과학교육과 / DKU / 예비 2번  최종등록 아주\n / ...
2991        건국\n 논술 최저 x  아주\n 논술 예비 2번 정외과  단국\n 논술 예...
2992                             경희\n / 원자력공학과 / 논술 전형   
Name: new_col, Length: 2993, dtype: object


In [4]:
# 1번 입시결과 요약 줄넘김 코드

import pandas as pd

# CSV 파일 불러오기
data = pd.read_csv('수만휘_칼럼분류.csv')

# "1. 입시결과 요약" 열에서 텍스트 끊어서 "new_col"에 저장
results = []
summary_column = data['1. 입시결과 요약']
for text in summary_column:
    if pd.notnull(text):  # NaN 값이 아닌 경우에만 처리
        # 대나 대학교가 포함된 단어 앞에서 줄넘김 처리
        lines = []
        current_line = ''
        for word in text.split():
            if '대' in word or '대학교' in word:
                if current_line:
                    lines.append(current_line)
                current_line = word
            else:
                current_line += ' ' + word
        if current_line:
            lines.append(current_line)
        formatted_text = '\n'.join(lines)
        results.append(formatted_text)

# "new_col" 열을 DataFrame에 추가
data['new_col'] = results

# 결과 출력
print(data['new_col'])

# 새로운 CSV 파일로 저장
data.to_csv('새로운_파일경로.csv', index=False, encoding='utf-8-sig')


0       한양대 정책학과 일반 - 불합\n경희대 사회학과 교과 - 불합\n시립대 도시사회학과...
1                                                        
2                                              예비\n아주대 화공
3       고려대 수학과 학우 학종 1차 불합\n한양대 수학과 학종 불합\n경희대 수학과 네오...
4       충북대 도시공학과 일반 교과 최초합\n전북대 도시공학과 일반 교과 최초합\n충남대 ...
                              ...                        
2988    가천대 식품생명공학과 사회기여자전형 - 1단계 합격 예비3번\n가천대 자유전공학부 ...
2989    한국교원대학교 일반사회교육과 학생부종합전형 예비14번9번까지 추합됨11번까지 추합됨...
2990    단국대 죽전 / 과학교육과 / DKU / 예비 2번 최종등록\n아주대 / 생명과학과...
2991    건국대 논술 최저 x\n아주대 논술 예비 2번 정외과\n단국대 논술 예비 92 사학...
2992                                 경희대 / 원자력공학과 / 논술 전형
Name: new_col, Length: 2993, dtype: object


In [10]:
import pandas as pd

# CSV 파일 불러오기
data = pd.read_csv('새로운_파일경로.csv')

# 새로운 칼럼 생성
max_columns = 10  # 최대 칼럼 개수 제한
num_lines = data['new_col'].str.count('\n')  # 줄넘김 개수
num_lines[num_lines > max_columns] = max_columns  # 최대 칼럼 개수 제한
new_columns = [f"대학{i+1}" for i in range(max_columns)]  # 칼럼 이름 생성

# 새로운 칼럼 추가
for column in new_columns:
    data[column] = ""

# 값 저장
for i, text in enumerate(data['new_col']):
    if pd.notnull(text):
        lines = text.split('\n')
        for j in range(max_columns):
            if j < num_lines[i]:
                data[new_columns[j]][i] = lines[j]

# 새로운 CSV 파일로 저장
data.to_csv('대학 구분 칼럼 생성 파일.csv', index=False, encoding='utf-8-sig')


C:\Users\dlxod\AppData\Local\Temp\ipykernel_5996\186321401.py:22: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data[new_columns[j]][i] = lines[j]
C:\Users\dlxod\AppData\Local\Temp\ipykernel_5996\186321401.py:22: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data[new_columns[j]][i] = lines[j]
C:\Users\dlxod\AppData\Local\Temp\ipykernel_5996\186321401.py:22: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data[new_columns[j]][i] = lines[j

In [15]:
import pandas as pd

# CSV 파일 불러오기
data = pd.read_csv('대학 구분 칼럼 생성 파일.csv')

# 결측치 개수 출력
num_missing_values = data.iloc[:, 20:34].isnull().sum()
print(num_missing_values)

# 총 row 개수 출력
num_rows = len(data)
print("총 row 개수:", num_rows)

# 21번째 열부터 34번째 열까지 결측치 비율 출력
for column in data.columns[20:34]:
    num_missing = data[column].isnull().sum()
    missing_ratio = num_missing / len(data) * 100
    print(f"{column}: 결측치 비율 = {missing_ratio:.2f}%")



대학6     2263
대학7     2633
대학8     2731
대학9     2793
대학10    2836
대학11    2866
대학12    2890
대학13    2912
대학14    2923
대학15    2936
대학16    2943
대학17    2956
대학18    2960
대학19    2965
dtype: int64
총 row 개수: 2993
대학6: 결측치 비율 = 75.61%
대학7: 결측치 비율 = 87.97%
대학8: 결측치 비율 = 91.25%
대학9: 결측치 비율 = 93.32%
대학10: 결측치 비율 = 94.75%
대학11: 결측치 비율 = 95.76%
대학12: 결측치 비율 = 96.56%
대학13: 결측치 비율 = 97.29%
대학14: 결측치 비율 = 97.66%
대학15: 결측치 비율 = 98.10%
대학16: 결측치 비율 = 98.33%
대학17: 결측치 비율 = 98.76%
대학18: 결측치 비율 = 98.90%
대학19: 결측치 비율 = 99.06%
